<a href="https://colab.research.google.com/github/michel-vbarboza/ERA5-Temperature-Prediction/blob/main/Local_XGBoost_(GPU).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Setup

In [ ]:
!pip install optuna -q

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 380.1/380.1 kB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.0/233.0 kB 20.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 7.6 MB/s eta 0:00:00


In [ ]:
import pickle
import pandas as pd
import cudf
from sklearn.metrics import mean_squared_error
import xgboost as xgb
import optuna

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
path = '/content/drive/MyDrive/MMEAD Dissertacao/Dados/'

# Preprocessing

In [ ]:
with open(path+'list_train.pkl', 'rb') as f:
    list_train = pickle.load(f)

with open(path+'list_test.pkl', 'rb') as f:
    list_test = pickle.load(f)

del f

In [ ]:
targets = ['target_1', 'target_3', 'target_5',
           'target_7', 'target_10', 'target_15']

features = list_train[0].columns.difference(targets)

In [ ]:
list_val = [df[df.index.year >= 2018] for df in list_train]
list_tr = [df[df.index.year < 2018] for df in list_train]

In [ ]:
target = 'target_15'

In [ ]:
list_X_tr = [df[features] for df in list_tr]
list_y_tr = [df[target] for df in list_tr]

list_X_val = [df[features] for df in list_val]
list_y_val = [df[target] for df in list_val]

list_X_train = [df[features] for df in list_train]
list_y_train = [df[target] for df in list_train]

list_X_test = [df[features] for df in list_test]
list_y_test = [df[target] for df in list_test]

In [ ]:
# Convert data to cuDF format
list_cudf_X_train = [cudf.DataFrame(df) for df in list_X_train]
list_cudf_y_train = [cudf.DataFrame(df) for df in list_y_train]

list_cudf_X_tr = [cudf.DataFrame(df) for df in list_X_tr]
list_cudf_y_tr = [cudf.DataFrame(df) for df in list_y_tr]

list_cudf_X_val = [cudf.DataFrame(df) for df in list_X_val]
list_cudf_y_val = [cudf.DataFrame(df) for df in list_y_val]

list_cudf_X_test = [cudf.DataFrame(df) for df in list_X_test]
list_cudf_y_test = [cudf.DataFrame(df) for df in list_y_test]

# Gradient Boosting

In [ ]:
list_best_params = []
list_pred = []
list_rmse = []

for i in range(len(list_train)):
    # Define the objective function for Optuna
    def objective(trial):
        # Suggest hyperparameters
        params = {
            'booster': 'gbtree',
            'objective': 'reg:squarederror',
            'eta': trial.suggest_float('eta', 0.001, 0.5, log=True),
            'max_depth': trial.suggest_int('max_depth', 3, 15),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.3, 1.0),
            'eval_metric': 'rmse',
            'device': 'cuda'
        }

        # Convert cuDF DataFrames to DMatrix, which is the data structure used by XGBoost
        dtrain = xgb.DMatrix(data=list_cudf_X_tr[i], label=list_cudf_y_tr[i])
        dval = xgb.DMatrix(data=list_cudf_X_val[i], label=list_cudf_y_val[i])

        # Train the model
        evallist = [(dtrain, 'train'), (dval, 'eval')]
        num_round = trial.suggest_int('num_round', 50, 200)
        bst = xgb.train(params, dtrain, num_round, evals=evallist, early_stopping_rounds=10, verbose_eval=False)

        # Predict on the validation set
        y_val_pred = bst.predict(dval)

        # Calculate RMSE for the validation set
        rmse_val = mean_squared_error(list_cudf_y_val[i].to_numpy(), y_val_pred, squared=False)

        return rmse_val


    # Create a study and optimize the objective function
    study = optuna.create_study(direction='minimize')
    study.optimize(objective, n_trials=50, n_jobs=-1)

    # Print the best parameters
    print(f'Best parameters: {study.best_params}')

    # Train the model with the best parameters on the entire training data
    best_params = study.best_params
    best_params['device'] = 'cuda'
    list_best_params.append(best_params)
    dtrain_full = xgb.DMatrix(data=list_cudf_X_train[i], label=list_cudf_y_train[i])
    dtest = xgb.DMatrix(data=list_cudf_X_test[i], label=list_cudf_y_test[i])
    bst = xgb.train(best_params, dtrain_full)

    # Predict on the test set
    y_test_pred = bst.predict(dtest)
    list_pred.append(y_test_pred)

    # Calculate RMSE for the test set
    rmse_test = mean_squared_error(list_cudf_y_test[i].to_numpy(), y_test_pred, squared=False)
    print(f'Test RMSE: {rmse_test}')
    list_rmse.append(rmse_test)

    print(f'LOOPING!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!: {i}')


# Save lists using pickle
with open(path+'list_pred_xgb_'+target+'.pkl', 'wb') as f:
    pickle.dump(list_pred, f)

with open(path+'list_rmse_xgb_'+target+'.pkl', 'wb') as f:
    pickle.dump(list_rmse, f)

with open(path+'list_best_params_xgb_'+target+'.pkl', 'wb') as f:
    pickle.dump(list_best_params, f)

[I 2024-08-20 16:58:40,477] A new study created in memory with name: no-name-05689cab-07fa-4bea-a9d2-2576917ab25f
[I 2024-08-20 16:58:41,589] Trial 6 finished with value: 1.2165344141930818 and parameters: {'eta': 0.09155412400819526, 'max_depth': 3, 'subsample': 0.6494239920596142, 'colsample_bytree': 0.664316738445577, 'num_round': 78}. Best is trial 6 with value: 1.2165344141930818.
[I 2024-08-20 16:58:41,619] Trial 0 finished with value: 1.2644204960779952 and parameters: {'eta': 0.03970290242753183, 'max_depth': 3, 'subsample': 0.8920440010580701, 'colsample_bytree': 0.8615268451780078, 'num_round': 80}. Best is trial 6 with value: 1.2165344141930818.
[I 2024-08-20 16:58:41,633] Trial 2 finished with value: 1.4574882324718472 and parameters: {'eta': 0.4753555149671905, 'max_depth': 10, 'subsample': 0.8303222063041173, 'colsample_bytree': 0.5776324377728739, 'num_round': 166}. Best is trial 6 with value: 1.2165344141930818.
[I 2024-08-20 16:58:42,554] Trial 1 finished with value: 2

Best parameters: {'eta': 0.04784428240004603, 'max_depth': 4, 'subsample': 0.6199311917380226, 'colsample_bytree': 0.8255038984851152, 'num_round': 170}
Test RMSE: 1.7007738403068016
LOOPING!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!: 0


[I 2024-08-20 16:59:16,706] Trial 4 finished with value: 1.265179702566145 and parameters: {'eta': 0.4293439640802528, 'max_depth': 4, 'subsample': 0.7922500575086333, 'colsample_bytree': 0.412304142366357, 'num_round': 161}. Best is trial 4 with value: 1.265179702566145.
[I 2024-08-20 16:59:17,140] Trial 0 finished with value: 1.7619702379375364 and parameters: {'eta': 0.015030367097675365, 'max_depth': 5, 'subsample': 0.7323161835482404, 'colsample_bytree': 0.326310829127511, 'num_round': 61}. Best is trial 4 with value: 1.265179702566145.
[I 2024-08-20 16:59:17,238] Trial 2 finished with value: 1.1879526132457057 and parameters: {'eta': 0.09304142501491415, 'max_depth': 4, 'subsample': 0.8502427189873891, 'colsample_bytree': 0.9464967166916105, 'num_round': 79}. Best is trial 2 with value: 1.1879526132457057.
[I 2024-08-20 16:59:17,699] Trial 5 finished with value: 1.455243598531517 and parameters: {'eta': 0.009054158515073981, 'max_depth': 3, 'subsample': 0.5772291565541954, 'colsa

Best parameters: {'eta': 0.08045111933822187, 'max_depth': 4, 'subsample': 0.7140361408065194, 'colsample_bytree': 0.6160570536022285, 'num_round': 147}
Test RMSE: 1.5436101753902616
LOOPING!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!: 1


[I 2024-08-20 16:59:57,716] Trial 4 finished with value: 1.3059671377173843 and parameters: {'eta': 0.42809122864654237, 'max_depth': 6, 'subsample': 0.8868534947647406, 'colsample_bytree': 0.663679540200234, 'num_round': 105}. Best is trial 4 with value: 1.3059671377173843.
[I 2024-08-20 16:59:58,233] Trial 6 finished with value: 1.3170516115583746 and parameters: {'eta': 0.32468517926134316, 'max_depth': 8, 'subsample': 0.9095885628332883, 'colsample_bytree': 0.981901793577052, 'num_round': 81}. Best is trial 4 with value: 1.3059671377173843.
[I 2024-08-20 16:59:58,561] Trial 1 finished with value: 1.405978761745662 and parameters: {'eta': 0.3246490390573682, 'max_depth': 10, 'subsample': 0.8181953037894936, 'colsample_bytree': 0.6812632676452641, 'num_round': 164}. Best is trial 4 with value: 1.3059671377173843.
[I 2024-08-20 16:59:58,752] Trial 3 finished with value: 1.2115039085899257 and parameters: {'eta': 0.02669104316687039, 'max_depth': 3, 'subsample': 0.8130858846442308, 'co

...

[I 2024-08-20 20:25:05,423] A new study created in memory with name: no-name-4c2d8cd9-b4f9-4d19-9ea4-313f7a1b0144


Test RMSE: 5.217394257608753
LOOPING!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!: 291


[I 2024-08-20 20:25:06,430] Trial 3 finished with value: 4.712330931236439 and parameters: {'eta': 0.015107900630855754, 'max_depth': 4, 'subsample': 0.7541557552695959, 'colsample_bytree': 0.6012002094289881, 'num_round': 65}. Best is trial 3 with value: 4.712330931236439.
[I 2024-08-20 20:25:06,494] Trial 4 finished with value: 3.8758901153147494 and parameters: {'eta': 0.20411536761137164, 'max_depth': 8, 'subsample': 0.9355828389182193, 'colsample_bytree': 0.5243255893220242, 'num_round': 108}. Best is trial 4 with value: 3.8758901153147494.
[I 2024-08-20 20:25:06,609] Trial 6 finished with value: 5.069870589248967 and parameters: {'eta': 0.009777531798398973, 'max_depth': 4, 'subsample': 0.9592127650477926, 'colsample_bytree': 0.51264100391123, 'num_round': 83}. Best is trial 4 with value: 3.8758901153147494.
[I 2024-08-20 20:25:06,773] Trial 5 finished with value: 4.894741110657438 and parameters: {'eta': 0.4167826225185849, 'max_depth': 11, 'subsample': 0.5066621623730738, 'cols

Best parameters: {'eta': 0.11802230968192438, 'max_depth': 9, 'subsample': 0.7921003245532622, 'colsample_bytree': 0.57696541958662, 'num_round': 81}
Test RMSE: 3.8620267041562077
LOOPING!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!: 292


[I 2024-08-20 20:25:44,953] Trial 2 finished with value: 4.487554606797196 and parameters: {'eta': 0.373752502607144, 'max_depth': 9, 'subsample': 0.5146591630316905, 'colsample_bytree': 0.5756885078665178, 'num_round': 122}. Best is trial 2 with value: 4.487554606797196.
[I 2024-08-20 20:25:45,037] Trial 4 finished with value: 3.7678041698248945 and parameters: {'eta': 0.11718571232437426, 'max_depth': 6, 'subsample': 0.8905389134786976, 'colsample_bytree': 0.9132723247086956, 'num_round': 132}. Best is trial 4 with value: 3.7678041698248945.
[I 2024-08-20 20:25:45,516] Trial 7 finished with value: 6.21786084530794 and parameters: {'eta': 0.0013998697861898521, 'max_depth': 3, 'subsample': 0.553394752197919, 'colsample_bytree': 0.9873128251889005, 'num_round': 127}. Best is trial 4 with value: 3.7678041698248945.
[I 2024-08-20 20:25:46,640] Trial 3 finished with value: 6.1499703599217 and parameters: {'eta': 0.0012688460124370832, 'max_depth': 5, 'subsample': 0.8302593920431002, 'cols

In [ ]:
import statistics
statistics.mean(list_rmse)

4.193720106126135

# Concurrent

In [ ]:
import concurrent.futures

def train_and_evaluate_model(index, list_cudf_X_tr, list_cudf_y_tr, list_cudf_X_val, list_cudf_y_val,
                             list_cudf_X_train, list_cudf_y_train, list_cudf_X_test, list_cudf_y_test,
                             list_best_params, list_pred, list_rmse):
    def objective(trial):
        # Suggest hyperparameters
        params = {
            'booster': 'gbtree',
            'objective': 'reg:squarederror',
            'eta': trial.suggest_float('eta', 0.001, 0.5, log=True),
            'max_depth': trial.suggest_int('max_depth', 3, 15),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.3, 1.0),
            'eval_metric': 'rmse',
            'tree_method': 'hist',  # Use the histogram method
            'device': 'cuda'  # Ensure GPU is used
        }

        # Convert cuDF DataFrames to DMatrix
        dtrain = xgb.DMatrix(data=list_cudf_X_tr[index], label=list_cudf_y_tr[index])
        dval = xgb.DMatrix(data=list_cudf_X_val[index], label=list_cudf_y_val[index])

        # Train the model
        evallist = [(dtrain, 'train'), (dval, 'eval')]
        num_round = trial.suggest_int('num_round', 50, 200)
        bst = xgb.train(params, dtrain, num_round, evals=evallist, early_stopping_rounds=10, verbose_eval=False)

        # Predict on the validation set
        y_val_pred = bst.predict(dval)

        # Calculate RMSE for the validation set
        rmse_val = mean_squared_error(list_cudf_y_val[index].to_numpy(), y_val_pred, squared=False)

        return rmse_val

    # Create a study and optimize the objective function
    study = optuna.create_study(direction='minimize')
    study.optimize(objective, n_trials=50)

    # Print the best parameters
    print(f'Index {index} Best parameters: {study.best_params}')

    # Train the model with the best parameters on the entire training data
    best_params = study.best_params
    best_params['tree_method'] = 'hist'
    best_params['device'] = 'cuda'
    list_best_params[index] = best_params

    dtrain_full = xgb.DMatrix(data=list_cudf_X_train[index], label=list_cudf_y_train[index])
    dtest = xgb.DMatrix(data=list_cudf_X_test[index], label=list_cudf_y_test[index])
    bst = xgb.train(best_params, dtrain_full, n_estimators=best_params['num_round'])

    # Predict on the test set
    y_test_pred = bst.predict(dtest)
    list_pred[index] = y_test_pred

    # Calculate RMSE for the test set
    rmse_test = mean_squared_error(list_cudf_y_test[index].to_numpy(), y_test_pred, squared=False)
    print(f'Index {index} Test RMSE: {rmse_test}')
    list_rmse[index] = rmse_test

    print(f'LOOPING!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!: {i}')

# Lists to store results
list_best_params = [None] * len(list_train)
list_pred = [None] * len(list_train)
list_rmse = [None] * len(list_train)

# Use ThreadPoolExecutor to run training in parallel
with concurrent.futures.ThreadPoolExecutor() as executor:
    futures = [executor.submit(train_and_evaluate_model, i, list_cudf_X_tr, list_cudf_y_tr,
                               list_cudf_X_val, list_cudf_y_val, list_cudf_X_train,
                               list_cudf_y_train, list_cudf_X_test, list_cudf_y_test,
                               list_best_params, list_pred, list_rmse)
               for i in range(len(list_train))]

    # Wait for all futures to complete
    concurrent.futures.wait(futures)

# Save lists using pickle
with open(path+'list_pred_xgb_'+target+'.pkl', 'wb') as f:
    pickle.dump(list_pred, f)

with open(path+'list_rmse_xgb_'+target+'.pkl', 'wb') as f:
    pickle.dump(list_rmse, f)

with open(path+'list_best_params_xgb_'+target+'.pkl', 'wb') as f:
    pickle.dump(list_best_params, f)